Transport equation
\begin{align}
    \partial_t c + \nabla \cdot (cu - k\nabla c) &= f &\mbox{ in }& \Omega\times (0,T],\label{eq:transport1}\\
    \nabla c\cdot n &= 0 &\mbox{ in }& \partial \Omega\times (0,T], \label{eq:transportBC}\\
    c(x,0) &= c_0(x) &\mbox{ in }&\Omega,
\end{align}
Crank-Nicolson method:
$$M\frac{C^{k+1}-C^k}{\Delta t}+\frac{1}{2}A[ C^{k+1}+C^k]=\frac{1}{2}(f^{k+1}+f^k)$$
or in an incremental form:
$$(M+0.5\Delta t A)(C^{k+1}-C^k)=-\Delta tAC^k+0.5\Delta t(f^{k+1}+f^k)$$

In [2]:
import netgen.gui
from ngsolve import *
from math import pi 
from netgen.geom2d import unit_square
mesh = Mesh(unit_square.GenerateMesh(maxh=0.2))

Draw(mesh)
mesh.nv, mesh.ne   # number of vertices & elements
print ("boundary labels: ", mesh.GetBoundaries())

Tend = 1 # End time
dt = 0.01 # Initial time step
t = Parameter(0.0)

#D(u)=kk*I
kk=1

#c exact
cexact = CoefficientFunction(sin(2*pi*(x-t))*cos(2*pi*(y-t)))
cinit  = CoefficientFunction(sin(2*pi*(x))*cos(2*pi*(y)))
cend   = CoefficientFunction(sin(2*pi*(x-Tend))*cos(2*pi*(y-Tend)))
Draw(cend,mesh,"cexact")
#gradient of c
c_dx =  2*pi*cos(2*pi*(x-t))*cos(2*pi*(y-t))
c_dy = -2*pi*sin(2*pi*(x-t))*sin(2*pi*(y-t))
c_dt =  2*pi*sin(2*pi*(x-t))*sin(2*pi*(y-t))- 2*pi*cos(2*pi*(x-t))*cos(2*pi*(y-t))
grad_cexact = CoefficientFunction((c_dx, c_dy))
grad_cexact_t =CoefficientFunction(c_dt)

#fixed velocity
u   = CoefficientFunction((1, 2))

cu  = cexact*u
dif = cu - kk*grad_cexact
div = dif[0].Diff(x) + dif[1].Diff(y)
#source f
source= grad_cexact_t + div

#print(force.dim)
#print(dif.dim)
#function spaces
k=2
l=2
C    = L2(mesh, order=l)
Cbar = FacetFESpace(mesh, order=l)
X    = FESpace([C, Cbar])

c, cbar = X.TrialFunction()
w, wbar = X.TestFunction()

gfu = GridFunction(X)

# Penalty parameter
beta_c = 6*l**2
beta_f = 10*k**2
n = specialcf.normal(mesh.dim)
h = specialcf.mesh_size

#Bilinear Form
a = BilinearForm(X)
Bha_dx = (c*u)*grad(w)
Bha_ds = c*u*n*(w-wbar)
Bha_ds_in = (u*n)*(c-cbar)*(w-wbar)

Bhd_dx = kk*grad(c)*grad(w)
Bhd_ds = - (kk*grad(c))*n*(w-wbar) + (beta_c/h)*(kk*n)*(c-cbar)*((w-wbar)*n)\
         - (kk*grad(w))*n*(c-cbar)

a += (Bha_dx + Bhd_dx)*dx
a += (Bha_ds + Bhd_ds - IfPos(u*n,0,1)*Bha_ds_in)*dx(element_boundary=True)
a.Assemble()

#Mstar=M+0.5*dt*A
m = BilinearForm(X, symmetric=False)
m += c*w*dx
m.Assemble()
mstar = m.mat.CreateMatrix()
mstar.AsVector().data = m.mat.AsVector() + 0.5*dt* a.mat.AsVector()
invmstar = mstar.Inverse(freedofs=X.FreeDofs(),inverse="umfpack")

f = LinearForm(X)
f += source*w*dx
#f += cinit*w*dx



boundary labels:  ('bottom', 'right', 'top', 'left')


In [3]:
#Tend=1
time = 0
t.Set(0)
t_intermediate = 0 
#initial
gfu.components[0].Set(cinit)
gfu.components[1].Set(sin(2*pi*x)*cos(2*pi*y), BND, definedon=mesh.Boundaries("right|left|top|bottom"))
res = gfu.vec.CreateVector()
while t_intermediate < Tend-0.5*dt:
    #Update time parameter
    t.Set(time+t_intermediate+dt)
    f.Assemble()
    
    #RHS: 1/2*dt*(f^(n+1)+f^(n))-dt*A*C^(k)
    res.data = 0.5*dt * (f.vec+f.vec) - dt * a.mat * gfu.vec
    gfu.vec.data += invmstar * res
        
    t_intermediate += dt
    #print("\r", time + t_intermediate,   end="")
    Redraw(blocking=True)

time += t_intermediate

#L2 error
err = sqrt(Integrate((gfu.components[0]-cexact)**2, mesh))
#err = sqrt(Integrate((gfu.components[0]-cend)**2, mesh))
print("\n error c:", err)
Draw(gfu.components[0],mesh,"c")



 error c: 0.48082229351380734
